In [97]:
## Libraries
import requests
from bs4 import BeautifulSoup
import json
import pandas as pd
import numpy as np
from pandas.core.frame import DataFrame
from math import log, floor

import plotly.express as px
from plotly.subplots import make_subplots
import plotly.graph_objects as go

pd.set_option('display.max_rows', None)
pd.set_option('display.max_columns', None)

import country_converter as coco

### USASpending API Request  

In [411]:
payload_0 =   {
      "filters": {
          "time_period": [
              {
                  "start_date": "2013-10-01",##FY2022: 2021-10-01---2022-09-30
                  "end_date": "2014-09-30"
              }],
                   "award_type_codes": [## set the category of grants
                    "02",
                    "03",
                    "04",
                    "05"
                   ]},
      "category": "country",
      "limit": 100,
      "page": 1
  }

response_result=[] 

while payload_0:
    print("-----")
    print("Requesting",payload_0)
    url='https://api.usaspending.gov/api/v2/search/spending_by_category/country'
    headers={"content-type":"application/json"}
    payload = json.dumps(payload_0)
    response = requests.post(url=url, data=payload,headers=headers)
    
    ##grab the new list
    response_result_0=json.loads(response.text)['results']
    ##store the results 
    response_result.extend(response_result_0)
    
    ##update the request
    response_next_page=json.loads(response.text)['page_metadata']["hasNext"]
    if response_next_page != False :
        response_page=json.loads(response.text)['page_metadata']['page'] + 1
        payload_0 =   {
      "filters": {
          "time_period": [
              {
                  "start_date": "2013-10-01",##FY2022
                  "end_date": "2014-09-30"
              }],
                   "award_type_codes": [## set the category of grants
                    "02",
                    "03",
                    "04",
                    "05"
                   ]},
      "category": "country",
      "limit": 100,
      "page": response_page }
    else:
        break

-----
Requesting {'filters': {'time_period': [{'start_date': '2013-10-01', 'end_date': '2014-09-30'}], 'award_type_codes': ['02', '03', '04', '05']}, 'category': 'country', 'limit': 100, 'page': 1}
-----
Requesting {'filters': {'time_period': [{'start_date': '2013-10-01', 'end_date': '2014-09-30'}], 'award_type_codes': ['02', '03', '04', '05']}, 'category': 'country', 'limit': 100, 'page': 2}


In [412]:
#response_result

[{'amount': 589601314522.66,
  'code': 'USA',
  'id': None,
  'name': 'UNITED STATES'},
 {'amount': 1296080695.0, 'code': 'CHE', 'id': None, 'name': 'SWITZERLAND'},
 {'amount': 795575270.0, 'code': 'ITA', 'id': None, 'name': 'ITALY'},
 {'amount': 578123362.0, 'code': 'SYR', 'id': None, 'name': 'SYRIA'},
 {'amount': 451592337.0, 'code': 'ZAF', 'id': None, 'name': 'SOUTH AFRICA'},
 {'amount': 448468998.0, 'code': 'AFG', 'id': None, 'name': 'AFGHANISTAN'},
 {'amount': 447203086.0, 'code': 'ETH', 'id': None, 'name': 'ETHIOPIA'},
 {'amount': 443335819.0, 'code': 'JOR', 'id': None, 'name': 'JORDAN'},
 {'amount': 436825836.39, 'code': 'KEN', 'id': None, 'name': 'KENYA'},
 {'amount': 433286235.61, 'code': 'NGA', 'id': None, 'name': 'NIGERIA'},
 {'amount': 388693003.03, 'code': 'UGA', 'id': None, 'name': 'UGANDA'},
 {'amount': 299497748.06, 'code': 'TZA', 'id': None, 'name': 'TANZANIA'},
 {'amount': 284969019.0, 'code': 'SSD', 'id': None, 'name': 'SOUTH SUDAN'},
 {'amount': 282871264.0,
  'code

In [413]:
# check the total transactions 
len(response_result)

189

In [414]:
# clean the request results 
data_response_0 = [[d["amount"],d["code"],d["name"]] for d in response_result]
country_grants = pd.DataFrame(data_response_0,columns = ["amount","code","name"])
country_grants["standard_names"] = coco.convert(names=country_grants["name"], to='name_short')
#drop value=0 row in specific columns 
country_grants_0 = country_grants.loc[country_grants['amount'] > 0]

In [398]:
#country_grants_0

amount code                                  name  \
0    6.071562e+11  USA                         UNITED STATES   
1    8.134061e+08  CHE                           SWITZERLAND   
2    6.870971e+08  ITA                                 ITALY   
3    6.689101e+08  AFG                           AFGHANISTAN   
4    6.551416e+08  SYR                                 SYRIA   
5    6.141240e+08  ETH                              ETHIOPIA   
6    4.857800e+08  LBR                               LIBERIA   
7    3.979615e+08  NGA                               NIGERIA   
8    3.930101e+08  UGA                                UGANDA   
9    3.776649e+08  KEN                                 KENYA   
10   3.533807e+08  ZAF                          SOUTH AFRICA   
11   3.522696e+08  TZA                              TANZANIA   
12   3.460429e+08  CAF              CENTRAL AFRICAN REPUBLIC   
13   3.389176e+08  GHA                                 GHANA   
14   3.014189e+08  SLV                           EL SALVADOR   
15   2.788288e+08  JOR                                JORDAN   
16   2.525681e+08  SDN                                 SUDAN   
17   2.465714e+08  PAK                              PAKISTAN   
18   2.446582e+08  HTI                                 HAITI   
19   2.277160e+08  SSD                           SOUTH SUDAN   
20   1.719533e+08  GIN                                GUINEA   
21   1.595869e+08  COD                      CONGO (KINSHASA)   
22   1.559867e+08  MOZ                            MOZAMBIQUE   
23   1.539544e+08  SLE                          SIERRA LEONE   
24   1.497547e+08  EGY                                 EGYPT   
25   1.447567e+08  RWA                                RWANDA   
26   1.431450e+08  BGD                            BANGLADESH   
27   1.370352e+08  MWI                                MALAWI   
28   1.369440e+08  IRQ                                  IRAQ   
29   1.112886e+08  DOM                    DOMINICAN REPUBLIC   
30   1.105485e+08  ZMB                                ZAMBIA   
31   1.010691e+08  SOM                               SOMALIA   
32   1.009780e+08  ZWE                              ZIMBABWE   
33   9.839649e+07  NPL                                 NEPAL   
34   9.815280e+07  BWA                              BOTSWANA   
35   9.778899e+07  GBR                        UNITED KINGDOM   
36   9.400357e+07  CAN                                CANADA   
37   9.094893e+07  MLI                                  MALI   
38   9.071306e+07  BEN                                 BENIN   
39   8.595852e+07  COL                              COLOMBIA   
40   8.363897e+07  SEN                               SENEGAL   
41   8.244434e+07  LBN                               LEBANON   
42   7.860555e+07  MMR                                 BURMA   
43   7.310205e+07  THA                              THAILAND   
44   7.292118e+07  YEM                                 YEMEN   
45   7.248549e+07  IND                                 INDIA   
46   7.111773e+07  GTM                             GUATEMALA   
47   6.620193e+07  UKR                               UKRAINE   
48   6.296436e+07  VNM                               VIETNAM   
49   6.205719e+07  CMR                              CAMEROON   
50   5.622913e+07  PHL                           PHILIPPINES   
51   5.411010e+07  COG                   CONGO (BRAZZAVILLE)   
52   5.385105e+07  HND                              HONDURAS   
53   5.173106e+07  MEX                                MEXICO   
54   5.099360e+07  IDN                             INDONESIA   
55   4.880183e+07  KHM                              CAMBODIA   
56   4.168970e+07  CIV                         COTE D'IVOIRE   
57   3.850142e+07  TUN                               TUNISIA   
58   3.784876e+07  PER                                  PERU   
59   3.450065e+07  NER                                 NIGER   
60   3.329171e+07  TUR                                TURKEY   
61   3.324306e+07  BFA                     

In [415]:
country_grants_0.shape

(185, 4)

### WIKIPEDIA List of countries and dependencies by population
+ https://en.wikipedia.org/wiki/List_of_countries_and_dependencies_by_population

In [179]:
country_list_2 = pd.read_csv("WIKI_country_list(population).csv")

In [181]:
#country_list_2 

In [416]:
merge4 = country_grants_0.merge(country_list_2,how="left",left_on="standard_names",right_on="standard_names")

In [417]:
##filter the columns 
merge5 = merge4.filter(["amount","code","standard_names","UN Region","Population","Date"])
##change the name of the column 
merge6_withUSA = merge5.rename(columns={"amount":"Amount","standard_names":"Country Name","Date":"Population Date"})
##log the numbers 
merge6_withUSA["log_Population"] = merge6_withUSA["Population"]
# log the numbers
merge6_withUSA["log_Population"] = np.log10(merge6_withUSA["Population"])
merge6_withoutUSA = merge6_withUSA.loc[~(merge6_withUSA["Country Name"]=="United States"),:]

In [366]:
#merge6_withoutUSA

Amount code                 Country Name UN Region    Population  \
1    1.130973e+09  CHE                  Switzerland    Europe  8.753933e+06   
2    6.490164e+08  SYR                        Syria      Asia  1.827600e+07   
3    5.735252e+08  ITA                        Italy    Europe  5.890674e+07   
4    5.544212e+08  ETH                     Ethiopia    Africa  1.208127e+08   
5    5.525612e+08  UGA                       Uganda    Africa  4.288590e+07   
6    5.488451e+08  NGA                      Nigeria    Africa  2.167469e+08   
7    5.047787e+08  KEN                        Kenya    Africa  4.756430e+07   
8    5.040162e+08  KOR                  South Korea      Asia  5.174500e+07   
9    4.627906e+08  SSD                  South Sudan    Africa  1.324992e+07   
10   4.621294e+08  ZAF                 South Africa    Africa  6.014298e+07   
11   4.495873e+08  MAR                      Morocco    Africa  3.666479e+07   
12   4.330131e+08  IRQ                         Iraq      Asia  4.119070e+07   
13   3.972273e+08  BEN                        Benin    Africa  1.250635e+07   
14   3.406396e+08  TZA                     Tanzania    Africa  5.944199e+07   
15   3.309912e+08  YEM                        Yemen      Asia  3.049100e+07   
16   3.228479e+08  AFG                  Afghanistan      Asia  3.289017e+07   
17   3.151234e+08  SOM                      Somalia    Africa  1.636000e+07   
18   2.414554e+08  ZMB                       Zambia    Africa  1.840056e+07   
19   2.334335e+08  PAK                     Pakistan      Asia  2.294890e+08   
20   2.249307e+08  COD                     DR Congo    Africa  9.237800e+07   
21   2.227279e+08  MOZ                   Mozambique    Africa  3.161608e+07   
22   2.060725e+08  HTI                        Haiti  Americas  1.174302e+07   
23   1.967658e+08  SDN                        Sudan    Africa  4.460127e+07   
24   1.708210e+08  BGD                   Bangladesh      Asia  1.682200e+08   
25   1.551569e+08  GTM                    Guatemala  Americas  1.710975e+07   
26   1.501407e+08  JOR                       Jordan      Asia  1.125611e+07   
27   1.451935e+08  ZWE                     Zimbabwe    Africa  1.579072e+07   
28   1.448550e+08  LBR                      Liberia    Africa  4.661010e+06   
29   1.373506e+08  MWI                       Malawi    Africa  2.150772e+07   
30   1.285433e+08  NPL                        Nepal      Asia  2.919248e+07   
31   1.263037e+08  UKR                      Ukraine    Europe  4.113043e+07   
32   1.230244e+08  COL                     Colombia  Americas  5.104950e+07   
33   1.210288e+08  GHA                        Ghana    Africa  3.083202e+07   
34   1.192436e+08  GBR               United Kingdom    Europe  6.708123e+07   
35   1.179043e+08  MLI                         Mali    Africa  2.147376e+07   
36   1.123659e+08  LBN                      Lebanon      Asia  6.769000e+06   
37   1.119178e+08  CAF     Central African Republic    Africa  5.633412e+06   
38   1.107307e+08  CAN                       Canada  Americas  3.882364e+07   
39   1.048102e+08  BWA                     Botswana    Africa  2.410338e+06   
40   9.370586e+07  SEN                      Senegal    Africa  1.722350e+07   
41   9.284974e+07  NER                        Niger    Africa  2.411275e+07   
42   9.179931e+07  RWA                       Rwanda    Africa  1.295577e+07   
43   7.480492e+07  THA                     Thailand      Asia  6.681333e+07   
44   7.307253e+07  CMR                     Cameroon    Africa  2.434825e+07   
45   7.200950e+07  LAO                         Laos      Asia  7.337783e+06   
46   6.931349e+07  XWB                    Palestine      Asia  5.227193e+06   
47   6.753810e+07  HND                     Honduras  Americas  9.546178e+06   
48   6.718826e+07  EGY                        Egypt    Africa  1.035963e+08   
49   6.665958e+07  MMR                      Myanmar      Asia  5.529498e+07   
50   6.368297e+07  MEX                       Mexico  Americas

In [418]:
merge6_withoutUSA = merge6_withoutUSA.rename(columns={"Population":"Total Population"})
merge6_withoutUSA_filtered = merge6_withoutUSA.filter(["Country Name","UN Region","Amount","Total Population","Population Date","log_Population"])

In [419]:
merge6_withoutUSA_filtered.shape

(185, 6)

In [420]:
merge6_withoutUSA_filtered = merge6_withoutUSA_filtered.dropna()

In [421]:
merge6_withoutUSA_filtered.shape

(184, 6)

In [422]:
def human_format(number):
    units = ['', 'K', 'M', 'G', 'T', 'P']
    k = 1000.0
    magnitude = int(floor(log(number, k)))
    return '%.2f%s' % (number / k**magnitude, units[magnitude])

In [423]:
#merge9["id"] = merge9["Country Name"].apply(lambda x:country_id_map[x])
merge6_withoutUSA_filtered['Amount '] = merge6_withoutUSA_filtered['Amount'].apply(lambda x:human_format(x))
merge6_withoutUSA_filtered['Population '] = merge6_withoutUSA_filtered['Total Population'].apply(lambda x:human_format(x))
#merge6_withoutUSA_filtered['Population '] = merge6_withoutUSA_filtered['Total Population'].apply(lambda x: x if np.isnan(x)else human_format(x))

In [373]:
#merge6_withoutUSA_filtered

Country Name UN Region        Amount  Total Population  \
1                 Switzerland    Europe  1.130973e+09      8.753933e+06   
2                       Syria      Asia  6.490164e+08      1.827600e+07   
3                       Italy    Europe  5.735252e+08      5.890674e+07   
4                    Ethiopia    Africa  5.544212e+08      1.208127e+08   
5                      Uganda    Africa  5.525612e+08      4.288590e+07   
6                     Nigeria    Africa  5.488451e+08      2.167469e+08   
7                       Kenya    Africa  5.047787e+08      4.756430e+07   
8                 South Korea      Asia  5.040162e+08      5.174500e+07   
9                 South Sudan    Africa  4.627906e+08      1.324992e+07   
10               South Africa    Africa  4.621294e+08      6.014298e+07   
11                    Morocco    Africa  4.495873e+08      3.666479e+07   
12                       Iraq      Asia  4.330131e+08      4.119070e+07   
13                      Benin    Africa  3.972273e+08      1.250635e+07   
14                   Tanzania    Africa  3.406396e+08      5.944199e+07   
15                      Yemen      Asia  3.309912e+08      3.049100e+07   
16                Afghanistan      Asia  3.228479e+08      3.289017e+07   
17                    Somalia    Africa  3.151234e+08      1.636000e+07   
18                     Zambia    Africa  2.414554e+08      1.840056e+07   
19                   Pakistan      Asia  2.334335e+08      2.294890e+08   
20                   DR Congo    Africa  2.249307e+08      9.237800e+07   
21                 Mozambique    Africa  2.227279e+08      3.161608e+07   
22                      Haiti  Americas  2.060725e+08      1.174302e+07   
23                      Sudan    Africa  1.967658e+08      4.460127e+07   
24                 Bangladesh      Asia  1.708210e+08      1.682200e+08   
25                  Guatemala  Americas  1.551569e+08      1.710975e+07   
26                     Jordan      Asia  1.501407e+08      1.125611e+07   
27                   Zimbabwe    Africa  1.451935e+08      1.579072e+07   
28                    Liberia    Africa  1.448550e+08      4.661010e+06   
29                     Malawi    Africa  1.373506e+08      2.150772e+07   
30                      Nepal      Asia  1.285433e+08      2.919248e+07   
31                    Ukraine    Europe  1.263037e+08      4.113043e+07   
32                   Colombia  Americas  1.230244e+08      5.104950e+07   
33                      Ghana    Africa  1.210288e+08      3.083202e+07   
34             United Kingdom    Europe  1.192436e+08      6.708123e+07   
35                       Mali    Africa  1.179043e+08      2.147376e+07   
36                    Lebanon      Asia  1.123659e+08      6.769000e+06   
37   Central African Republic    Africa  1.119178e+08      5.633412e+06   
38                     Canada  Americas  1.107307e+08      3.882364e+07   
39                   Botswana    Africa  1.048102e+08      2.410338e+06   
40                    Senegal    Africa  9.370586e+07      1.722350e+07   
41                      Niger    Africa  9.284974e+07      2.411275e+07   
42                     Rwanda    Africa  9.179931e+07      1.295577e+07   
43                   Thailand      Asia  7.480492e+07      6.681333e+07   
44                   Cameroon    Africa  7.307253e+07      2.434825e+07   
45                       Laos      Asia  7.200950e+07      7.337783e+06   
46                  Palestine      Asia  6.931349e+07      5.227193e+06   
47                   Honduras  Americas  6.753810e+07      9.546178e+06   
48                      Egypt    Africa  6.718826e+07      1.035963e+08   
49                    Myanmar      Asia  6.665958e+07      5.529498e+07   
50                     Mexico  Americas  6.368297e+07      1.282712e+08   
51                    Vietnam      Asia  6.237307e+07      9.850540e+07   
52                El Salvador  Americas  6.199805e+07      6.825935e+06   
53              Cote d'Ivoire    Africa  6

In [426]:
#aa = merge6_withoutUSA_filtered["Amount "].tolist()
merge6_withoutUSA_filtered.to_csv('2014grants_withoutUSA.csv')

In [17]:
#merge6_withoutUSA_filtered = merge6_withoutUSA.filter(["Country Name","UN Region","Amount","Population","Population Date"])
# hover_data = {"Amount": False,
#                                 "log_Population": False,
#                                "Total Population": False,
#                                "Population Date": True,
#                                "Amount_int": True,
#                                "Population_int": True}

In [424]:
fig = px.sunburst(merge6_withoutUSA_filtered,path=["UN Region","Country Name"],values = "Amount",hover_name = "UN Region",color = "log_Population"
            , title = "Distribution of US Grants Spending in FY2022"
                  ,color_continuous_scale="magma",
                  hover_data = {"Amount": False,
                                "log_Population":False,
                                "Amount ": True,
                               "Population ": True}
           , labels={'log_Population': 'Population'})
fig.update_layout(margin={"r":0,"t":40,"l":0,"b":0})
#fig.update_traces(hovertemplate='Amount: %{aa} <br>Population: %{Population .tolist()}') 
fig.show()

### Geographical Map  

In [273]:
## Read in geojson
all_country = json.load(open("all_country.geojson","r"))

In [148]:
#all_country["features"]

In [275]:
# prepare for plotting
country_id_map = {}
for feature in all_country["features"]:
    feature["properties"]['name']= coco.convert(names=feature["properties"]['name'], to='name_short')
    feature["id"] = feature["properties"]['name']
    country_id_map[feature["properties"]['name']] = feature["id"]

In [276]:
##list the countires in the gepjson file 
list = []
list.extend(country_id_map)
list_0 = {"geo_list_0": list}
geo_list = DataFrame(list_0)

In [277]:
## merge dfs
merge7 = geo_list.merge(merge6_withoutUSA_filtered,how="left",left_on="geo_list_0",right_on="Country Name")

In [278]:
#merge7

geo_list_0              Country Name UN Region  \
0                    Afghanistan               Afghanistan      Asia   
1                         Angola                    Angola    Africa   
2                        Albania                   Albania    Europe   
3           United Arab Emirates      United Arab Emirates      Asia   
4                      Argentina                 Argentina  Americas   
5                        Armenia                   Armenia      Asia   
6    French Southern Territories                       NaN       NaN   
7                      Australia                 Australia   Oceania   
8                        Austria                   Austria    Europe   
9                     Azerbaijan                Azerbaijan      Asia   
10                       Burundi                   Burundi    Africa   
11                       Belgium                   Belgium    Europe   
12                         Benin                     Benin    Africa   
13                  Burkina Faso              Burkina Faso    Africa   
14                    Bangladesh                Bangladesh      Asia   
15                      Bulgaria                  Bulgaria    Europe   
16                       Bahamas                   Bahamas  Americas   
17        Bosnia and Herzegovina    Bosnia and Herzegovina    Europe   
18                       Belarus                   Belarus    Europe   
19                        Belize                    Belize  Americas   
20                       Bermuda                   Bermuda  Americas   
21                       Bolivia                   Bolivia  Americas   
22                        Brazil                    Brazil  Americas   
23             Brunei Darussalam         Brunei Darussalam      Asia   
24                        Bhutan                    Bhutan      Asia   
25                      Botswana                  Botswana    Africa   
26      Central African Republic  Central African Republic    Africa   
27                        Canada                    Canada  Americas   
28                   Switzerland               Switzerland    Europe   
29                         Chile                     Chile  Americas   
30                         China                     China      Asia   
31                 Cote d'Ivoire             Cote d'Ivoire    Africa   
32                      Cameroon                  Cameroon    Africa   
33                      DR Congo                  DR Congo    Africa   
34                Congo Republic            Congo Republic    Africa   
35                      Colombia                  Colombia  Americas   
36                    Costa Rica                Costa Rica  Americas   
37                        Kosovo                    Kosovo    Europe   
38                          Cuba                      Cuba  Americas   
39                        Cyprus                    Cyprus      Asia   
40                        Cyprus                    Cyprus      Asia   
41                Czech Republic            Czech Republic    Europe   
42                       Germany                   Germany    Europe   
43                      Djibouti                  Djibouti    Africa   
44                       Denmark                   Denmark    Europe   
45            Dominican Republic        Dominican Republic  Americas   
46                       Algeria                   Algeria    Africa   
47                       Ecuador                   Ecuador  Americas   
48                         Egypt                     Egypt    Africa   
49                       Eritrea                       NaN       NaN   
50                Western Sahara            Western Sahara    Africa   
51                         Spain                     Spain    Europe   
52                       Estonia                   Estonia    Europe   
53                      Ethiopia                  Ethiopia    Africa   
54                       Finland                   Finland    

In [279]:
merge8 = merge7.filter(["geo_list_0","Amount","UN Region","Total Population","Amount ","Population","Population ","Population Date"])
merge9 = merge8.rename(columns={"geo_list_0":"Country Name"})

In [280]:
merge9["id"] = merge9["Country Name"].apply(lambda x:country_id_map[x])

In [281]:
# log the numbers
merge9["log_Grants Amount"] = np.log10(merge9["Amount"])
#merge9

Country Name        Amount UN Region  Total Population  \
0                    Afghanistan  3.295451e+08      Asia      3.289017e+07   
1                         Angola  2.226311e+07    Africa      3.308628e+07   
2                        Albania  9.865109e+06    Europe      2.829741e+06   
3           United Arab Emirates  5.957150e+06      Asia      9.282410e+06   
4                      Argentina  3.709323e+06  Americas      4.732741e+07   
5                        Armenia  2.139479e+07      Asia      2.963900e+06   
6    French Southern Territories           NaN       NaN               NaN   
7                      Australia  4.058117e+07   Oceania      2.592097e+07   
8                        Austria  8.499572e+06    Europe      9.027999e+06   
9                     Azerbaijan  6.940461e+06      Asia      1.016446e+07   
10                       Burundi  2.997002e+07    Africa      1.257457e+07   
11                       Belgium  2.772635e+06    Europe      1.165762e+07   
12                         Benin  2.936965e+07    Africa      1.250635e+07   
13                  Burkina Faso  1.297686e+08    Africa      2.151018e+07   
14                    Bangladesh  3.433910e+08      Asia      1.682200e+08   
15                      Bulgaria  3.146860e+06    Europe      6.520314e+06   
16                       Bahamas  1.535720e+06  Americas      3.934500e+05   
17        Bosnia and Herzegovina  3.483238e+07    Europe      3.320954e+06   
18                       Belarus  8.126537e+06    Europe      9.349645e+06   
19                        Belize  2.140872e+06  Americas      4.301910e+05   
20                       Bermuda  1.066542e+07  Americas      6.405500e+04   
21                       Bolivia  7.307666e+06  Americas      1.179726e+07   
22                        Brazil  4.385376e+07  Americas      2.149029e+08   
23             Brunei Darussalam  1.854790e+05      Asia      4.299990e+05   
24                        Bhutan  1.128348e+06      Asia      7.632000e+05   
25                      Botswana  5.693773e+07    Africa      2.410338e+06   
26      Central African Republic  1.125642e+08    Africa      5.633412e+06   
27                        Canada  1.109073e+08  Americas      3.882364e+07   
28                   Switzerland  3.442878e+09    Europe      8.753933e+06   
29                         Chile  5.730674e+06  Americas      1.967836e+07   
30                         China  1.308480e+07      Asia      1.412600e+09   
31                 Cote d'Ivoire  9.444051e+07    Africa      2.708773e+07   
32                      Cameroon  1.309069e+08    Africa      2.434825e+07   
33                      DR Congo  6.359433e+08    Africa      9.237800e+07   
34                Congo Republic  6.518012e+06    Africa      5.657000e+06   
35                      Colombia  3.476689e+08  Americas      5.104950e+07   
36                    Costa Rica  2.809639e+07  Americas      5.163038e+06   
37                        Kosovo  1.198802e+07    Europe      1.798188e+06   
38                          Cuba  4.379159e+06  Americas      1.111322e+07   
39                        Cyprus  2.891974e+05      Asia      9.181000e+05   
40                        Cyprus  2.891974e+05      Asia      3.822300e+05   
41                Czech Republic  4.303634e+06    Europe      1.051671e+07   
42                       Germany  9.670328e+06    Europe      8.369543e+07   
43                      Djibouti  1.343366e+07    Africa      9.761070e+05   
44                       Denmark  4.546435e+06    Europe      5.883562e+06   
45            Dominican Republic  6.262198e+07  Americas      1.053554e+07   
46                       Algeria  4.571042e+06    Africa      4.540000e+07   
47                       Ecuador  8.097923e+07  Americas      1.802321e+07   
48                         Egypt  8.247229e+07    Africa      1.035963e+08   
49                       Eritrea           NaN       NaN               NaN   
50                Western Sahara  5.000000

In [225]:
#merge9.to_csv('2022geomap_data.csv')

In [282]:
# plot 
fig = px.choropleth_mapbox(merge9,
                    locations = "id",
                    geojson = all_country,
                    color="log_Grants Amount",
                   hover_name = "Country Name",
                   #hover_data = merge9.columns,
                    hover_data = {"id": False,
                                "log_Grants Amount":False,
                                "Amount ": True,
                               "Population ": True,
                                "Population Date": True},
                     mapbox_style = "carto-positron",
                    color_continuous_scale="magma",
                     zoom= 0.57,opacity = 0.3,
                    center = {"lat": 34.55,"lon":18.04},
                    title = "Distribution of USA Grants Spending around the world in FY2022"
                 ,labels={'log_Grants Amount': 'Grants Amount'}
                    )
fig.update_layout(margin={"r":0,"t":40,"l":0,"b":0})
fig.show()

### Shared Prosperity  
+ https://www.worldbank.org/en/topic/poverty/brief/global-database-of-shared-prosperity

In [231]:
SSI = pd.read_csv("SSI.csv")

In [232]:
SSI["standerd_name"]= coco.convert(names=SSI["countryname"], to='name_short')

In [234]:
## merge dfs
merge_ssi = geo_list.merge(SSI,how="left",left_on="geo_list_0",right_on="standerd_name")

In [235]:
#merge_ssi

geo_list_0           countryname  Bottom 40%  \
0                    Afghanistan                   NaN         NaN   
1                         Angola                   NaN         NaN   
2                        Albania               Albania        8.81   
3           United Arab Emirates  United Arab Emirates        7.08   
4                      Argentina             Argentina       -5.66   
5                        Armenia               Armenia        1.26   
6    French Southern Territories                   NaN         NaN   
7                      Australia                   NaN         NaN   
8                        Austria               Austria        1.10   
9                     Azerbaijan                   NaN         NaN   
10                       Burundi                   NaN         NaN   
11                       Belgium               Belgium        2.15   
12                         Benin                   NaN         NaN   
13                  Burkina Faso                   NaN         NaN   
14                    Bangladesh                   NaN         NaN   
15                      Bulgaria              Bulgaria        8.95   
16                       Bahamas                   NaN         NaN   
17        Bosnia and Herzegovina                   NaN         NaN   
18                       Belarus               Belarus        1.11   
19                        Belize                   NaN         NaN   
20                       Bermuda                   NaN         NaN   
21                       Bolivia               Bolivia        2.25   
22                        Brazil                Brazil       -1.40   
23             Brunei Darussalam                   NaN         NaN   
24                        Bhutan                Bhutan        1.63   
25                      Botswana                   NaN         NaN   
26      Central African Republic                   NaN         NaN   
27                        Canada                Canada        1.43   
28                   Switzerland           Switzerland       -0.34   
29                         Chile                 Chile        1.92   
30                         China                 China        7.20   
31                 Cote d'Ivoire                   NaN         NaN   
32                      Cameroon                   NaN         NaN   
33                      DR Congo                   NaN         NaN   
34                Congo Republic                   NaN         NaN   
35                      Colombia              Colombia       -5.98   
36                    Costa Rica            Costa Rica       -3.18   
37                        Kosovo                Kosovo        2.36   
38                          Cuba                   NaN         NaN   
39                        Cyprus                Cyprus        5.17   
40                Czech Republic        Czech Republic        4.40   
41                       Germany               Germany        1.72   
42                      Djibouti                   NaN         NaN   
43                       Denmark               Denmark        1.66   
44            Dominican Republic                   NaN         NaN   
45                       Algeria                   NaN         NaN   
46                       Ecuador               Ecuador       -3.49   
47                         Egypt      Egypt, Arab Rep.       -2.50   
48                       Eritrea                   NaN         NaN   
49                Western Sahara                   NaN         NaN   
50                         Spain                 Spain        4.03   
51                       Estonia               Estonia        8.03   
52                      Ethiopia                   NaN         NaN   
53                       Finland               Finland        1.13   
54                          Fiji                   NaN         NaN   
55              Falkland Islands                   NaN         NaN   
56                        France

In [237]:
merge_ssi_1 = merge_ssi.filter(["geo_list_0","Bottom 40%"])
merge_ssi_2 = merge_ssi_1.rename(columns={"geo_list_0":"Country Name"})

In [240]:
merge_ssi_2["id"] = merge_ssi_2["Country Name"].apply(lambda x:country_id_map[x])
#merge_ssi_2

Country Name  Bottom 40%                           id
0                    Afghanistan         NaN                  Afghanistan
1                         Angola         NaN                       Angola
2                        Albania        8.81                      Albania
3           United Arab Emirates        7.08         United Arab Emirates
4                      Argentina       -5.66                    Argentina
5                        Armenia        1.26                      Armenia
6    French Southern Territories         NaN  French Southern Territories
7                      Australia         NaN                    Australia
8                        Austria        1.10                      Austria
9                     Azerbaijan         NaN                   Azerbaijan
10                       Burundi         NaN                      Burundi
11                       Belgium        2.15                      Belgium
12                         Benin         NaN                        Benin
13                  Burkina Faso         NaN                 Burkina Faso
14                    Bangladesh         NaN                   Bangladesh
15                      Bulgaria        8.95                     Bulgaria
16                       Bahamas         NaN                      Bahamas
17        Bosnia and Herzegovina         NaN       Bosnia and Herzegovina
18                       Belarus        1.11                      Belarus
19                        Belize         NaN                       Belize
20                       Bermuda         NaN                      Bermuda
21                       Bolivia        2.25                      Bolivia
22                        Brazil       -1.40                       Brazil
23             Brunei Darussalam         NaN            Brunei Darussalam
24                        Bhutan        1.63                       Bhutan
25                      Botswana         NaN                     Botswana
26      Central African Republic         NaN     Central African Republic
27                        Canada        1.43                       Canada
28                   Switzerland       -0.34                  Switzerland
29                         Chile        1.92                        Chile
30                         China        7.20                        China
31                 Cote d'Ivoire         NaN                Cote d'Ivoire
32                      Cameroon         NaN                     Cameroon
33                      DR Congo         NaN                     DR Congo
34                Congo Republic         NaN               Congo Republic
35                      Colombia       -5.98                     Colombia
36                    Costa Rica       -3.18                   Costa Rica
37                        Kosovo        2.36                       Kosovo
38                          Cuba         NaN                         Cuba
39                        Cyprus        5.17                       Cyprus
40                Czech Republic        4.40               Czech Republic
41                       Germany        1.72                      Germany
42                      Djibouti         NaN                     Djibouti
43                       Denmark        1.66                      Denmark
44            Dominican Republic         NaN           Dominican Republic
45                       Algeria         NaN                      Algeria
46                       Ecuador       -3.49                      Ecuador
47                         Egypt       -2.50                        Egypt
48                       Eritrea         NaN                      Eritrea
49                Western Sahara         NaN               Western Sahara
50                         Spain        4.03                        Spain
51                       Estonia        8.03                      Estonia
52                      Ethiopia         NaN                     Ethiopia
53                      

In [246]:
# plot 
fig = px.choropleth_mapbox(merge_ssi_2,
                    locations = "id",
                    geojson = all_country,
                    color="Bottom 40%",
                   hover_name = "Country Name",
                   #hover_data = merge9.columns,
                    hover_data = {"id": False,
                                "Bottom 40%":True},
                     mapbox_style = "carto-positron",
                    color_continuous_scale="magma",
                     zoom= 0.57,opacity = 0.3,
                    center = {"lat": 34.55,"lon":18.04},
                    title = "Map of Shared Prosperity"
                    )
fig.update_layout(margin={"r":0,"t":40,"l":0,"b":0})
fig.show()

### Grants increase rate 

In [435]:
import math

In [535]:
grants_withoutUSA2019 = pd.read_csv("2019grants_withoutUSA.csv")
grants_withoutUSA2014 = pd.read_csv("2014grants_withoutUSA.csv")

In [536]:
grants_withoutUSA2019["Year"] = "2019"
grants_withoutUSA2014["Year"] = "2014"

In [468]:
grants_withoutUSA2019.shape

(194, 10)

In [469]:
grants_withoutUSA2014.shape

(184, 10)

In [537]:
grants2014_2019=pd.merge(grants_withoutUSA2014,grants_withoutUSA2019, on='Country Name', how='outer')

In [471]:
grants2014_2019.shape

(201, 19)

In [538]:
grants2014_2019 = grants2014_2019.dropna()

In [473]:
grants2014_2019.shape

(181, 19)

In [539]:
#grants2014_2019

Unnamed: 0_x                    Country Name UN Region_x      Amount_x  \
0             1.0                     Switzerland      Europe  1.296081e+09   
1             2.0                           Italy      Europe  7.955753e+08   
2             3.0                           Syria        Asia  5.781234e+08   
3             4.0                    South Africa      Africa  4.515923e+08   
4             5.0                     Afghanistan        Asia  4.484690e+08   
5             6.0                        Ethiopia      Africa  4.472031e+08   
6             7.0                          Jordan        Asia  4.433358e+08   
7             8.0                           Kenya      Africa  4.368258e+08   
8             9.0                         Nigeria      Africa  4.332862e+08   
9            10.0                          Uganda      Africa  3.886930e+08   
10           11.0                        Tanzania      Africa  2.994977e+08   
11           12.0                     South Sudan      Africa  2.849690e+08   
12           13.0        Central African Republic      Africa  2.828713e+08   
13           14.0                        Pakistan        Asia  2.096908e+08   
14           15.0                           Sudan      Africa  2.085000e+08   
15           16.0                        DR Congo      Africa  1.751354e+08   
16           17.0                      Bangladesh        Asia  1.638060e+08   
17           18.0                      Mozambique      Africa  1.523392e+08   
18           19.0                           Ghana      Africa  1.521863e+08   
19           20.0                         Somalia      Africa  1.481046e+08   
20           21.0                           Egypt      Africa  1.313875e+08   
21           22.0                         Liberia      Africa  1.304424e+08   
22           23.0                           Haiti    Americas  1.282583e+08   
23           24.0                         Senegal      Africa  1.163397e+08   
24           25.0                          Zambia      Africa  1.121272e+08   
25           26.0                           India        Asia  1.109550e+08   
26           27.0                           Yemen        Asia  1.088714e+08   
27           28.0                     Philippines        Asia  1.078662e+08   
28           29.0                            Iraq        Asia  9.846156e+07   
29           30.0                           Niger      Africa  9.524057e+07   
30           31.0                        Colombia    Americas  9.287043e+07   
31           32.0                       Guatemala    Americas  9.143595e+07   
32           33.0                          Rwanda      Africa  8.784567e+07   
33           34.0                         Ukraine      Europe  8.579670e+07   
34           35.0                         Lebanon        Asia  8.549573e+07   
35           36.0                  United Kingdom      Europe  8.440930e+07   
36           37.0                          Canada    Americas  8.431805e+07   
37           38.0                     El Salvador    Americas  7.754368e+07   
38           39.0                          Malawi      Africa  7.724152e+07   
39           40.0                        Thailand        Asia  7.706325e+07   
40           41.0                        Zimbabwe      Africa  7.267520e+07   
41           42.0                           Nepal        Asia  6.602995e+07   
42           43.0                         Myanmar        Asia  6.333790e+07   
43           44.0                   Cote d'Ivoire      Africa  6.091381e+07   
44           45.0                          Turkey        Asia  5.910138e+07   
45           46.0                            Peru    Americas  5.880163e+07   
46           47.0                        Cambodia        Asia  5.780036e+07   
47           48.0                    Burkina Faso      Africa  5.753067e+07   
48           49.0                            Mali      Africa  5.559453e+07   
49           50.0                            Fiji     O

In [540]:
grants2014_2019["grants_ins_rate"] = round(((grants2014_2019["Amount_y"]/grants2014_2019["Amount_x"])**(1/5)-1)*100,3)

In [541]:
## merge dfs
merge_grants2014_2019 = geo_list.merge(grants2014_2019,how="left",left_on="geo_list_0",right_on="Country Name")

In [512]:
#merge_grants2014_2019

geo_list_0  Unnamed: 0_x              Country Name  \
0                    Afghanistan           5.0               Afghanistan   
1                         Angola          61.0                    Angola   
2                        Albania          99.0                   Albania   
3           United Arab Emirates         149.0      United Arab Emirates   
4                      Argentina         119.0                 Argentina   
5                        Armenia          76.0                   Armenia   
6    French Southern Territories           NaN                       NaN   
7                      Australia          73.0                 Australia   
8                        Austria          79.0                   Austria   
9                     Azerbaijan         108.0                Azerbaijan   
10                       Burundi          97.0                   Burundi   
11                       Belgium         134.0                   Belgium   
12                         Benin          59.0                     Benin   
13                  Burkina Faso          48.0              Burkina Faso   
14                    Bangladesh          17.0                Bangladesh   
15                      Bulgaria         118.0                  Bulgaria   
16                       Bahamas         121.0                   Bahamas   
17        Bosnia and Herzegovina          77.0    Bosnia and Herzegovina   
18                       Belarus         106.0                   Belarus   
19                        Belize         103.0                    Belize   
20                       Bermuda         100.0                   Bermuda   
21                       Bolivia         129.0                   Bolivia   
22                        Brazil          71.0                    Brazil   
23             Brunei Darussalam           NaN                       NaN   
24                        Bhutan         148.0                    Bhutan   
25                      Botswana          60.0                  Botswana   
26      Central African Republic          13.0  Central African Republic   
27                        Canada          37.0                    Canada   
28                   Switzerland           1.0               Switzerland   
29                         Chile         135.0                     Chile   
30                         China          65.0                     China   
31                 Cote d'Ivoire          44.0             Cote d'Ivoire   
32                      Cameroon          64.0                  Cameroon   
33                      DR Congo          16.0                  DR Congo   
34                Congo Republic          80.0            Congo Republic   
35                      Colombia          31.0                  Colombia   
36                    Costa Rica         109.0                Costa Rica   
37                        Kosovo         160.0                    Kosovo   
38                          Cuba         171.0                      Cuba   
39                        Cyprus         140.0                    Cyprus   
40                        Cyprus         140.0                    Cyprus   
41                        Cyprus         141.0                    Cyprus   
42                        Cyprus         141.0                    Cyprus   
43                Czech Republic          86.0            Czech Republic   
44                       Germany          91.0                   Germany   
45                      Djibouti         131.0                  Djibouti   
46                       Denmark         101.0                   Denmark   
47            Dominican Republic          83.0        Dominican Republic   
48                       Algeria         124.0                   Algeria   
49                       Ecuador          94.0                   Ecuador   
50                         Egypt          21.0                     Egypt   
51                       Eritrea           NaN                       N

In [542]:
merge_grants2014_2019 = merge_grants2014_2019.filter(["Country Name","grants_ins_rate","Amount _x","Amount _y","UN Region_x","Total Population_y"])
merge_grants2014_2019 = merge_grants2014_2019.rename(columns={"grants_ins_rate":"Annualized Growth Rate","Amount _x":"2014 Amount","Amount _y":"2019 Amount",
                                                             "UN Region_x":"UN Region","Total Population_y":"Total Population"})

In [543]:
merge_grants2014_2019 = merge_grants2014_2019.dropna()

In [544]:
#merge_grants2014_2019

Country Name  Annualized Growth Rate 2014 Amount 2019 Amount  \
0                 Afghanistan                  -8.713     448.47M     284.30M   
1                      Angola                  -1.955      30.77M      27.88M   
2                     Albania                   0.517       7.73M       7.94M   
3        United Arab Emirates                  13.532     625.80K       1.18M   
4                   Argentina                  22.850       3.33M       9.31M   
5                     Armenia                   0.681      15.44M      15.98M   
7                   Australia                  19.835      16.43M      40.59M   
8                     Austria                   8.876      13.04M      19.95M   
9                  Azerbaijan                  -3.251       4.95M       4.20M   
10                    Burundi                  27.323       8.70M      29.12M   
11                    Belgium                  14.957       1.86M       3.73M   
12                      Benin                  -4.714      31.64M      24.85M   
13               Burkina Faso                   2.874      57.53M      66.29M   
14                 Bangladesh                   9.965     163.81M     263.39M   
15                   Bulgaria                 -31.091       3.52M     546.60K   
16                    Bahamas                  43.370       3.17M      19.21M   
17     Bosnia and Herzegovina                  10.808      14.60M      24.39M   
18                    Belarus                   7.438       5.18M       7.41M   
19                     Belize                 -27.204       7.00M       1.43M   
20                    Bermuda                  -1.062       7.40M       7.02M   
21                    Bolivia                   9.282       2.21M       3.44M   
22                     Brazil                  19.472      17.84M      43.43M   
24                     Bhutan                  34.112     650.01K       2.82M   
25                   Botswana                  -4.827      30.93M      24.15M   
26   Central African Republic                 -20.311     282.87M      90.90M   
27                     Canada                   4.659      84.32M     105.88M   
28                Switzerland                   1.617       1.30G       1.40G   
29                      Chile                  18.847       1.73M       4.10M   
30                      China                  -4.265      23.15M      18.62M   
31              Cote d'Ivoire                  56.033      60.91M     563.38M   
32                   Cameroon                  29.682      27.25M      99.93M   
33                   DR Congo                  26.572     175.14M     568.93M   
34             Congo Republic                   4.821      12.30M      15.57M   
35                   Colombia                  26.543      92.87M     301.34M   
36                 Costa Rica                  35.993       4.52M      21.03M   
37                     Kosovo                  95.259     293.75K       8.34M   
38                       Cuba                 123.859     116.75K       6.56M   
39                     Cyprus                 -17.413       1.25M     481.90K   
40                     Cyprus                 -17.413       1.25M     481.90K   
41                     Cyprus                 -17.413       1.25M     481.90K   
42                     Cyprus                 -17.413       1.25M     481.90K   
43             Czech Republic                 -15.976      10.86M       4.55M   
44                    Germany                   9.129      10.14M      15.69M   
45                   Djibouti                  17.322       2.16M       4.80M   
46                    Denmark                 -20.351       7.32M       2.35M   
47         Dominican Republic                  16.590      11.60M      24.99M   
48                    Algeria                  10.006       2.95M       4.75M   
49                    Ecuador                  40.073       9.33M      50.30M   
50                      Egypt                  -

In [568]:
#merge_grants2014_2019.to_csv('grants_rate_2014_2019.csv')

In [545]:
merge_grants2014_2019["id"] =merge_grants2014_2019["Country Name"].apply(lambda x:country_id_map[x])
#merge_grants2014_2019

Country Name  Annualized Growth Rate 2014 Amount 2019 Amount  \
0                 Afghanistan                  -8.713     448.47M     284.30M   
1                      Angola                  -1.955      30.77M      27.88M   
2                     Albania                   0.517       7.73M       7.94M   
3        United Arab Emirates                  13.532     625.80K       1.18M   
4                   Argentina                  22.850       3.33M       9.31M   
5                     Armenia                   0.681      15.44M      15.98M   
7                   Australia                  19.835      16.43M      40.59M   
8                     Austria                   8.876      13.04M      19.95M   
9                  Azerbaijan                  -3.251       4.95M       4.20M   
10                    Burundi                  27.323       8.70M      29.12M   
11                    Belgium                  14.957       1.86M       3.73M   
12                      Benin                  -4.714      31.64M      24.85M   
13               Burkina Faso                   2.874      57.53M      66.29M   
14                 Bangladesh                   9.965     163.81M     263.39M   
15                   Bulgaria                 -31.091       3.52M     546.60K   
16                    Bahamas                  43.370       3.17M      19.21M   
17     Bosnia and Herzegovina                  10.808      14.60M      24.39M   
18                    Belarus                   7.438       5.18M       7.41M   
19                     Belize                 -27.204       7.00M       1.43M   
20                    Bermuda                  -1.062       7.40M       7.02M   
21                    Bolivia                   9.282       2.21M       3.44M   
22                     Brazil                  19.472      17.84M      43.43M   
24                     Bhutan                  34.112     650.01K       2.82M   
25                   Botswana                  -4.827      30.93M      24.15M   
26   Central African Republic                 -20.311     282.87M      90.90M   
27                     Canada                   4.659      84.32M     105.88M   
28                Switzerland                   1.617       1.30G       1.40G   
29                      Chile                  18.847       1.73M       4.10M   
30                      China                  -4.265      23.15M      18.62M   
31              Cote d'Ivoire                  56.033      60.91M     563.38M   
32                   Cameroon                  29.682      27.25M      99.93M   
33                   DR Congo                  26.572     175.14M     568.93M   
34             Congo Republic                   4.821      12.30M      15.57M   
35                   Colombia                  26.543      92.87M     301.34M   
36                 Costa Rica                  35.993       4.52M      21.03M   
37                     Kosovo                  95.259     293.75K       8.34M   
38                       Cuba                 123.859     116.75K       6.56M   
39                     Cyprus                 -17.413       1.25M     481.90K   
40                     Cyprus                 -17.413       1.25M     481.90K   
41                     Cyprus                 -17.413       1.25M     481.90K   
42                     Cyprus                 -17.413       1.25M     481.90K   
43             Czech Republic                 -15.976      10.86M       4.55M   
44                    Germany                   9.129      10.14M      15.69M   
45                   Djibouti                  17.322       2.16M       4.80M   
46                    Denmark                 -20.351       7.32M       2.35M   
47         Dominican Republic                  16.590      11.60M      24.99M   
48                    Algeria                  10.006       2.95M       4.75M   
49                    Ecuador                  40.073       9.33M      50.30M   
50                      Egypt                  -

In [546]:
# plot 
fig = px.choropleth_mapbox(merge_grants2014_2019,
                    locations = "id",
                    geojson = all_country,
                    color="Annualized Growth Rate",
                   hover_name = "Country Name",
                   #hover_data = merge9.columns,
                    hover_data = {"id": False,
                                "Annualized Growth Rate":True,
                                 "2014 Amount":True,
                                 "2019 Amount":True},
                     mapbox_style = "carto-positron",
                    color_continuous_scale="magma",
                     zoom= 0.57,opacity = 0.3,
                    center = {"lat": 34.55,"lon":18.04},
                    title = "Map of FY 2014-2019 Grants Annualized Growth Rate"
                    ,labels={'Annualized Growth Rate': 'Grants Annualized Growth Rate'})
fig.update_layout(margin={"r":0,"t":40,"l":0,"b":0})
fig.show()

### Grants-SSI   

In [547]:
merge_grants2014_2019.shape

(166, 7)

In [548]:
grants2_inc_ssi=pd.merge(merge_grants2014_2019,merge_ssi_2, on='Country Name', how='outer')

In [549]:
#grants2_inc_ssi

Country Name  Annualized Growth Rate 2014 Amount  \
0                    Afghanistan                  -8.713     448.47M   
1                         Angola                  -1.955      30.77M   
2                        Albania                   0.517       7.73M   
3           United Arab Emirates                  13.532     625.80K   
4                      Argentina                  22.850       3.33M   
5                        Armenia                   0.681      15.44M   
6                      Australia                  19.835      16.43M   
7                        Austria                   8.876      13.04M   
8                     Azerbaijan                  -3.251       4.95M   
9                        Burundi                  27.323       8.70M   
10                       Belgium                  14.957       1.86M   
11                         Benin                  -4.714      31.64M   
12                  Burkina Faso                   2.874      57.53M   
13                    Bangladesh                   9.965     163.81M   
14                      Bulgaria                 -31.091       3.52M   
15                       Bahamas                  43.370       3.17M   
16        Bosnia and Herzegovina                  10.808      14.60M   
17                       Belarus                   7.438       5.18M   
18                        Belize                 -27.204       7.00M   
19                       Bermuda                  -1.062       7.40M   
20                       Bolivia                   9.282       2.21M   
21                        Brazil                  19.472      17.84M   
22                        Bhutan                  34.112     650.01K   
23                      Botswana                  -4.827      30.93M   
24      Central African Republic                 -20.311     282.87M   
25                        Canada                   4.659      84.32M   
26                   Switzerland                   1.617       1.30G   
27                         Chile                  18.847       1.73M   
28                         China                  -4.265      23.15M   
29                 Cote d'Ivoire                  56.033      60.91M   
30                      Cameroon                  29.682      27.25M   
31                      DR Congo                  26.572     175.14M   
32                Congo Republic                   4.821      12.30M   
33                      Colombia                  26.543      92.87M   
34                    Costa Rica                  35.993       4.52M   
35                        Kosovo                  95.259     293.75K   
36                          Cuba                 123.859     116.75K   
37                        Cyprus                 -17.413       1.25M   
38                        Cyprus                 -17.413       1.25M   
39                        Cyprus                 -17.413       1.25M   
40                        Cyprus                 -17.413       1.25M   
41                Czech Republic                 -15.976      10.86M   
42                       Germany                   9.129      10.14M   
43                      Djibouti                  17.322       2.16M   
44                       Denmark                 -20.351       7.32M   
45            Dominican Republic                  16.590      11.60M   
46                       Algeria                  10.006       2.95M   
47                       Ecuador                  40.073       9.33M   
48                         Egypt                  -7.337     131.39M   
49                         Spain                  29.632       1.71M   
50                       Estonia                 136.296      59.80K   
51                      Ethiopia                   9.753     447.20M   
52                       Finland                   2.572       2.44M   
53                          Fiji                 -50.602      53.23M   
54                        France                   8.546    

In [522]:
grants2_inc_ssi.shape

(180, 7)

In [550]:
grants2_inc_ssi = grants2_inc_ssi.dropna()

In [551]:
grants2_inc_ssi.shape

(77, 9)

In [552]:
grants2_inc_ssi_1 = grants2_inc_ssi.filter(["Country Name","Annualized Growth Rate","Bottom 40%","Total Population","UN Region"])

In [553]:
#grants2_inc_ssi_1

Country Name  Annualized Growth Rate  Bottom 40%  \
2                 Albania                   0.517        8.81   
3    United Arab Emirates                  13.532        7.08   
4               Argentina                  22.850       -5.66   
5                 Armenia                   0.681        1.26   
7                 Austria                   8.876        1.10   
10                Belgium                  14.957        2.15   
14               Bulgaria                 -31.091        8.95   
17                Belarus                   7.438        1.11   
20                Bolivia                   9.282        2.25   
21                 Brazil                  19.472       -1.40   
22                 Bhutan                  34.112        1.63   
25                 Canada                   4.659        1.43   
26            Switzerland                   1.617       -0.34   
27                  Chile                  18.847        1.92   
28                  China                  -4.265        7.20   
33               Colombia                  26.543       -5.98   
34             Costa Rica                  35.993       -3.18   
35                 Kosovo                  95.259        2.36   
37                 Cyprus                 -17.413        5.17   
38                 Cyprus                 -17.413        5.17   
39                 Cyprus                 -17.413        5.17   
40                 Cyprus                 -17.413        5.17   
41         Czech Republic                 -15.976        4.40   
42                Germany                   9.129        1.72   
44                Denmark                 -20.351        1.66   
47                Ecuador                  40.073       -3.49   
48                  Egypt                  -7.337       -2.50   
49                  Spain                  29.632        4.03   
50                Estonia                 136.296        8.03   
52                Finland                   2.572        1.13   
54                 France                   8.546        0.97   
56         United Kingdom                  -2.051        1.19   
57                Georgia                  16.824       -0.58   
63                 Greece                  46.978        5.08   
66               Honduras                  -6.312        1.00   
67                Croatia                  -3.088        8.08   
69                Hungary                   6.184        6.75   
70              Indonesia                  -8.875        4.78   
71                  India                  -8.308        4.48   
73                Iceland                 -14.839        5.65   
74                 Israel                 -14.947        3.69   
75                  Italy                 -30.363        1.02   
79             Kazakhstan                  -1.055       -0.30   
81        Kyrgyz Republic                  30.134        0.76   
85                   Laos                  -2.039        1.91   
91              Lithuania                  26.422        9.89   
92             Luxembourg                 -11.297       -0.68   
93                 Latvia                  59.117        7.19   
95                Moldova                   2.844        1.71   
97                 Mexico                  14.990        0.70   
98              Macedonia                  -9.535        7.03   
100                 Malta                  -3.122        2.93   
101               Myanmar                  14.453        9.46   
102            Montenegro                  89.290        3.43   
103              Mongolia                  -7.999       -3.70   
106                Malawi                  21.614       -2.96   
113           Netherlands                  48.069        2.57   
117              Pakistan                  -7.413        1.34   
118                Panama                  39.057        4.97   
119                  Peru                   5.832       -3.74   
120           Philippines                  -1.16

In [556]:
grants2_inc_ssi_1['Population'] = grants2_inc_ssi_1['Total Population'].apply(lambda x:human_format(x))

In [560]:
grants2_inc_ssi_1['Annualized Growth Rate(%)'] = grants2_inc_ssi_1["Annualized Growth Rate"].astype(str) + " %"

In [570]:
#grants2_inc_ssi_1.to_csv('grants2_inc_ssi.csv')

In [571]:
fig = px.scatter(grants2_inc_ssi_1, x="Annualized Growth Rate", y="Bottom 40%",
         size="Total Population", color="UN Region",
                 hover_name="Country Name", log_x=True, size_max=107,
                 hover_data = {"Total Population": False,
                                "Annualized Growth Rate":False,
                                 "Bottom 40%":True,
                                 "Annualized Growth Rate(%)":True,
                              "Population" : True}
                )
fig.update_layout(
    title='Grants Annualized Growth Rate v. Shared Prosperity',
    xaxis=dict(
        title='Grants Annualized Growth Rate (FY 2014-2019)',
        gridcolor='white',
        type='log',
        gridwidth=2,
    ),
    yaxis=dict(
        title='Bottom 40% Annualized Growth Rate of Income',
        gridcolor='white',
        gridwidth=2,
    ),
    paper_bgcolor='rgb(243, 243, 243)',
    plot_bgcolor='rgb(243, 243, 243)',
)
fig.show()